# Schools Count Exercise in Python

### Count Schools in Berlin using Overpass API through Python
This analysis uses the [OSMPythonTools](https://github.com/mocnik-science/osm-python-tools) to query the Overpass API. In addition [Nominatim](https://nominatim.org/) is queried first to define the area of interest.

In [1]:
from OSMPythonTools.overpass import Overpass
from OSMPythonTools.overpass import overpassQueryBuilder
from OSMPythonTools.nominatim import Nominatim

nominatim = Nominatim()
overpass = Overpass()

query = overpassQueryBuilder(
    area=nominatim.query('Berlin').areaId(),
    elementType=['node', 'way', 'relation'],
    selector=['"amenity"="school"']
)

result = overpass.query(query)

print(f"Nodes: {len(result.nodes())}")
print(f"Ways: {len(result.ways())}")
print(f"Relations: {len(result.relations())}")

[nominatim] downloading data: search
[overpass] downloading data: [timeout:25][out:json];area(3600062422)->.searchArea;(node["amenity"="school"](area.searchArea);way["amenity"="school"](area.searchArea);relation["amenity"="school"](area.searchArea);); out body;


Nodes: 131
Ways: 932
Relations: 21


### Count Schools per District using ohsome-py package
Here we use the [ohsome-py](https://github.com/GIScience/ohsome-py) package to query the ohsome API. We use the `elements/count/groupBy/boundary` endpoint. 

For this analysis we assume that you already downloaded the district boundaries for Berlin. If not do this via [OSM Boundaries](https://osm-boundaries.com/).

In [5]:
import json
import matplotlib.pyplot as plt
import pandas as pd
from ohsome import OhsomeClient
client = OhsomeClient()

infile = "../../data/berlin_districts.geojson"
with open(infile) as f:
    boundaries = json.load(f)
    
filter_schools = "amenity=school"
response = client.elements.count.groupByBoundary.post(
    bpolys=json.dumps(boundaries), 
    filter=filter_schools
)

schools_df = response.as_dataframe()
display(schools_df)

value
boundary  timestamp                       
feature1  2022-11-02 09:00:00+00:00   74.0
feature10 2022-11-02 09:00:00+00:00  107.0
feature11 2022-11-02 09:00:00+00:00   78.0
feature12 2022-11-02 09:00:00+00:00   84.0
feature2  2022-11-02 09:00:00+00:00  105.0
feature3  2022-11-02 09:00:00+00:00  133.0
feature4  2022-11-02 09:00:00+00:00   76.0
feature5  2022-11-02 09:00:00+00:00   80.0
feature6  2022-11-02 09:00:00+00:00   87.0
feature7  2022-11-02 09:00:00+00:00   92.0
feature8  2022-11-02 09:00:00+00:00   75.0
feature9  2022-11-02 09:00:00+00:00  100.0

### Count Schools in Berlin per district using ohsome API through Python
This example directly queries the ohsome API using Python's `request` module. As above we use this endpoint `elements/count/groupBy/boundary`. 

In [7]:
import json
from datetime import datetime
import requests

base_url = "https://api.ohsome.org/v1"
endpoint = "/elements/count/groupBy/boundary"
url = base_url + endpoint

# open geojson file
with open("../../data/berlin_districts.geojson", "r") as file:
    bpolys = json.load(file)

parameters = {
    "bpolys": json.dumps(bpolys),  # pass GeoJSON as string.
    "filter": "amenity=school",
    "format": "json",
    "time": "2022-01-01",
}

response = requests.post(url, data=parameters)
response.raise_for_status()  # Raise an Exception if HTTP Status Code is not 200

print("Response:")
print(json.dumps(response.json(), indent=4))  # Pretty print response

result = response.json()["groupByResult"]

Response:
{
    "attribution": {
        "url": "https://ohsome.org/copyrights",
        "text": "\u00a9 OpenStreetMap contributors"
    },
    "apiVersion": "1.7.0",
    "groupByResult": [
        {
            "groupByObject": "feature1",
            "result": [
                {
                    "timestamp": "2022-01-01T00:00:00Z",
                    "value": 72.0
                }
            ]
        },
        {
            "groupByObject": "feature2",
            "result": [
                {
                    "timestamp": "2022-01-01T00:00:00Z",
                    "value": 113.0
                }
            ]
        },
        {
            "groupByObject": "feature3",
            "result": [
                {
                    "timestamp": "2022-01-01T00:00:00Z",
                    "value": 141.0
                }
            ]
        },
        {
            "groupByObject": "feature4",
            "result": [
                {
                    "timestamp": "